# Практикум Python


<img src="https://www.python.org/static/community_logos/python-logo-master-v3-TM.png" align="right" style="height: 200px;"/>

# Работа с сетью. Клиенты и парсинг

In [1]:
# Убедитесь, что вотэтовотвсё установлено
import urllib, requests, socket, re, lxml, io, bs4, scrapy, sqlite3, pandas, sqlalchemy

In [3]:
!pip install lxml bs4 scrapy pandas sqlalchemy

# Как работает Интернет?

Два основных концепта:
- пакеты
- протоколы

**Пакет** - малый фрагмент большого сообщения. Каждый пакет несет полезные данные и информацию об этих данных (aka *заголовок*), благодаря которой получатель пакета понимает что с ним делать.

Пересылка данных выполняется следующим образом:
- данные разбиваются на набор пакетов
- пакеты преобразуются в биты (набор 0 и 1) и отправляются в сеть
- пакеты перемещаются по сети с помощью маршрутизирующих устройств (роутеры, свитчи)
- пакеты попадают на целевой компьютер
- целевой компьютер с помощью заголовков собирает из пакетов исходные данные

Пакеты передаются по сети с помощью **коммутации пакетов** (packet switching). Промежуточные роутеры и свитчи могут обрабатывать пакеты независимо, без учета откуда они пришли и куда направляются. Это приводит к тому, что ни одно соединение не является более приоритетным - в итоге это соединение не будет занимать единолично сетевое устройство.

Соединение двух компьютеров, у которых может быть разное "железо" и разные программы - одна из основных проблем, появившихся на заре Интернета. Необходимы правила передачи информации, которые были бы универсальны для всех компьютеров.

Эту проблемы удалось разрешить с помощью введения **протоколов** - стандатизированного способа выполнения определенных действий и форматирования данных, чтобы устройства могли друг друга понимать.

Существует огромное количество протоколов:
- для передачи пакетов между устройствами внутри одной сети (Ethernet)
- для передачи пакетов между сетями (IP)
- для гарантированной передачи пакетов в нужном порядке (TCP)
- для форматирования данных для вебсайтов и приложений (HTTP)

Помимо этих основных протоколов существует огромное количество других протоколов, которые используются для разных целей - маршрутизации, тестирования, шифрования и т.д.

## Пример - подключение к colab

Для отображения этой страницы компьютеры обмениваются тысячами пакетов, которые передаются по кабелям и волнам через роутеры и свитчи. Ваш компьютер получает эти пакеты и передает их в браузер, а затем браузер интерпретирует данные из пакетов, чтобы отобразить этот текст.

Какие шаги вовлечены в этот процесс:
- **Запрос в браузере.** Вы вбиваете URI ресурса, который вам нужен:
    
    `<схема>:[//[<логин>[:<пароль>]@]<хост>[:<порт>]][/<URL‐путь>][?<параметры>][#<якорь>]`  
- **DNS запрос.** Для идентификации компьютеров в сети используются IP адреса вида `127.0.0.1`. Эти адреса удобны для машин, но неудобны для людей (цифры неудобно запоминать) - намного удобнее использовать *доменные имена*, например, `google.com`. Чтобы сопоставлять IP адреса и доменные имена используются службы доменных имен (*Domain Name Service*, *DNS*). - они помогают по доменному имени получать IP адрес компьютера (не только это, но опустим).
- **TCP рукопожатие.** Браузер устанавлиевает соединение с этим IP адресом.
- **TLS рукопожатие.** Браузер также устанавливает шифрование с сервером, чтобы никто еще не смог прочитать данные из пакетов.
- **HTTP запрос.** Браузер запрашивает содержимое этой веб-страницы.
- **HTTP ответ.** Сервер отдает содержимое веб-страницы в виде HTML, CSS и JavaScript кода, разбитых на набор пакетов. Как только бразуер получает пакеты и проверяет их содержимое, он интерпретирует их как веб-страница, которую вы видите.

Весь процесс занимает 1-2 секунды.

## HTML



**HTML** (HyperText Markup Language) -- язык разметки, который используется для web-страниц.

Это механизм для получения структурного текста, который понимают браузеры.

Структура в тексте задаётся вложенными тегами, теги определяют то, как текст будет показан (отрендерен).

Это тег: `<тег>`, теги бывают открывающими (`<тег>`) и закрывающими (`</тег>`).

Пример HTML-разметки:

```html
<!DOCTYPE html>
<html>
   <head>
      <meta charset="utf-8" />
      <title>HTML Document</title>
   </head>
   <body>
      <p> <!-- p -- это параграф, а в такие странные скобки заключается комментарий -->
         <b>
            Этот текст будет полужирным, <i>а этот — ещё и курсивным</i>.
         </b>
      </p>
   </body>
</html>
```

Так он выглядит после рендеринга:

<!DOCTYPE html>
<html>
   <head>
      <meta charset="utf-8" />
      <title>HTML Document</title>
   </head>
   <body>
      <p> <!-- p -- это параграф, а в такие странные скобки заключается комментарий -->
         <b>
            Этот текст будет полужирным, <i>а этот — ещё и курсивным</i>.
         </b>
      </p>
   </body>
</html>

Видно, что HTML-разметка имеет древовидную структуру - каждый тег (вершина дерева) имеет 0 (тогда это лист дерева) или больше (тогда это внутренняя вершина) вложенных в него тегов.

Значит, чтобы доставать из HTML какую-то информацию, можно использовать его структуру.

Мы этим займёмся чуть позже.

А ещё у тегов бывают **атрибуты**:

```html
<a href="http://example.com">Ссылка на example.com</a>
```
Отрендерим этот кусок:
<a href="http://example.com">Ссылка на example.com</a>

А этот текст (безусловно, имеющий структуру), был написан с помощью другого языка разметки -- **Markdown**. [Руководство](https://paulradzkov.com/2014/markdown_cheatsheet/)

**P.S.**
На самом деле, такую же структуру имеет и формат XML (другой язык разметки).

Формально, HTML -- это более стандартизированное подмножество XML.

## HTTP

**HTTP** (HyperText Transfer Protocol) - протокол передачи гипертекста.

На самом деле, в HTTP мы передаём не только гипертекст, а **ресурсы** -- обобщение, куда попадает и гипертекст, и картинки, и музыка и т.д. Но стандарт подходит для всего этого.

Каждый ресурс имеет адрес -- **URI** (Uniform Resource Identifier) -- аналог пути в системе компьютера.

Не будем говорить про низкоуровневую сторону вопроса: стек TCP/IP, сокеты, порты и т.д.

Чтобы получить данные, клиент делает запрос на сервер. В запросе должны быть 3 части:
* Starting line -- определяет тип сообщения;
* Headers -- характеризуют тело сообщения, параметры передачи и прочие сведения;
* Message body -- непосредственно данные сообщения.

Ответное сообщение от сервера имеет такую же структуру.

Чтобы посылать эти запросы "руками", а не через браузер, можно использовать утилиту `curl`. Ей и воспользуемся.

In [ ]:
%%bash
curl example.com/index.html -v

<!doctype html>
<html>
<head>
    <title>Example Domain</title>

    <meta charset="utf-8" />
    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />
    <meta name="viewport" content="width=device-width, initial-scale=1" />
    <style type="text/css">
    body {
        background-color: #f0f0f2;
        margin: 0;
        padding: 0;
        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;
        
    }
    div {
        width: 600px;
        margin: 5em auto;
        padding: 2em;
        background-color: #fdfdff;
        border-radius: 0.5em;
        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);
    }
    a:link, a:visited {
        color: #38488f;
        text-decoration: none;
    }
    @media (max-width: 700px) {
        div {
            margin: 0 auto;
            width: auto;
        }
    }
    </style>    
</head>

<body>
<div>
    <h1>Example Domain</h1>
    <p>This domai

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0*   Trying 93.184.216.34:80...
* TCP_NODELAY set
* Connected to example.com (93.184.216.34) port 80 (#0)
> GET /index.html HTTP/1.1
> Host: example.com
> User-Agent: curl/7.68.0
> Accept: */*
> 
* Mark bundle as not supporting multiuse
< HTTP/1.1 200 OK
< Accept-Ranges: bytes
< Age: 370922
< Cache-Control: max-age=604800
< Content-Type: text/html; charset=UTF-8
< Date: Thu, 30 Mar 2023 08:13:45 GMT
< Etag: "3147526947"
< Expires: Thu, 06 Apr 2023 08:13:45 GMT
< Last-Modified: Thu, 17 Oct 2019 07:18:26 GMT
< Server: ECS (oxr/8324)
< Vary: Accept-Encoding
< X-Cache: HIT
< Content-Length: 1256
< 
{ [1256 bytes data]
100  1256  100  1256    0     0  66105      0 --:--:-- --:--:-- --:--:-- 66105
* Connection #0 to host example.com left intact


### Методы HTTP

HTTP метод определяет операцию, которую мы хотим произвести над ресурсом.

Самые частые методы: GET, POST, PUT, DELETE (но есть и другие).

* **GET** -- запрос содержимого ресурса. <br>GET-запросы идемпотентны. Поэтому они могут кэшироваться.
* **POST** -- передача данных на ресурс (например, при отправке комментария на форуме или вводе пароля на сайте). <br> Не идемпотентны => при отправке одного и того же комментария на форум он появится там дважды.  <br>Не кэшируются.
* **PUT** -- передача данных в конкретный URI (изменение существующего ресурса). Не кэшируются.
* **DELETE** -- удаление ресурса.

### Коды HTTP

В ответном сообщении придёт код ответа HTTP, который определяет результат выполнения операции.

Самые частые коды: `200 OK`, `400 BadRequest`, `404 Not Found`, `500 Internal Server Error`.

Общий обзор кодов:
* **1xx** -- Informational. Информационные коды, например, `102 Processing` (запрос пока обрабатывается);
* **2xx** -- Success. Успех. Всё хорошо, запрос отработал и ничего не сломал. По крайней мере, пока.
* **3xx** -- Redirection. Перенаправление на другой ресурс/страницу.
* **4xx** -- Client error. Ошибка клиента (неверные данные запроса или неправильный путь).
* **5xx** -- Server error. Что-то сломалось на сервере (там поделили на ноль, например).

### Разбор примера

Давайте ещё раз посмотрим на запрос к `example.com/index.html`.

Служебная информация от `curl`:

```
*   Trying 93.184.216.34...
* TCP_NODELAY set
* Connected to example.com (93.184.216.34) port 80 (#0)
```
Запрос клиента:
```
> GET /index.html HTTP/1.1    # Starting line: метод GET, URI -- /index.html, версия протокола -- HTTP/1.1
> Host: example.com           # Заголовки сообщения
> User-Agent: curl/7.58.0
> Accept: */*
>                             # Пустое тело, т.к. мы ничего не передали на сервер.
```

Ответ сервера:
```
< HTTP/1.1 200 OK                          # Starting line: версия протокола и код ответа
< Accept-Ranges: bytes                     # Заголовки ответа
< Age: 482235
< Cache-Control: max-age=6048000            
< Content-Type: text/html; charset=UTF-8
< Date: Wed, 27 Apr 2022 12:33:28 GMT
< Etag: "3147526947+gzip"
< Expires: Wed, 04 May 2022 12:33:28 GMT
< Last-Modified: Thu, 17 Oct 2019 07:18:26 GMT
< Server: ECS (nyb/1D10)
< Vary: Accept-Encoding
< X-Cache: HIT
< Content-Length: 1256
<                                          # Пустая строка -- нужна по стандарту
<!doctype html>                            # Тело ответа -- HTML-документ
<html>
<head>
    <title>Example Domain</title>
. . .
```


### Полезные ссылки

https://faun.pub/http-and-everything-you-need-to-know-about-it-8273bc224491 - доступно про HTTP (english)

# Web scraping

**Веб-скрапинг** - это технология получения веб-данных путем извлечения их со страниц веб-ресурсов.

Состоит из двух этапов:
* Получение html
* Парсинг html

Парсинг — автоматизированный сбор и систематизация данных. Его проводят с помощью программ, которые называются парсерами. Парсинг нужен, чтобы ускорить рутинную работу.
Парсить можно что угодно — цены конкурентов, поисковые фразы, аккаунты в соцсетях, битые ссылки.

## Получение html



Варианты инструментов:

* `urllib`
* `requests` (de-facto standard)
* `socket` (low-level)

### `urllib`

In [7]:
import urllib.request

In [9]:
#Открывает URL-адрес и читает ответ данные.
response = urllib.request.urlopen('http://example.com/')
html = response.read()
print(*[x for x in html.split(b'\n')], sep='\n')

b'<!doctype html>'
b'<html>'
b'<head>'
b'    <title>Example Domain</title>'
b''
b'    <meta charset="utf-8" />'
b'    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />'
b'    <meta name="viewport" content="width=device-width, initial-scale=1" />'
b'    <style type="text/css">'
b'    body {'
b'        background-color: #f0f0f2;'
b'        margin: 0;'
b'        padding: 0;'
b'        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;'
b'        '
b'    }'
b'    div {'
b'        width: 600px;'
b'        margin: 5em auto;'
b'        padding: 2em;'
b'        background-color: #fdfdff;'
b'        border-radius: 0.5em;'
b'        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);'
b'    }'
b'    a:link, a:visited {'
b'        color: #38488f;'
b'        text-decoration: none;'
b'    }'
b'    @media (max-width: 700px) {'
b'        div {'
b'            margin: 0 auto;'
b'            width: auto;'
b'  

In [11]:
type(html)

bytes

In [13]:
type(response)

http.client.HTTPResponse

In [15]:
html = html.decode('utf-8')
print(html)

<!doctype html>
<html>
<head>
    <title>Example Domain</title>

    <meta charset="utf-8" />
    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />
    <meta name="viewport" content="width=device-width, initial-scale=1" />
    <style type="text/css">
    body {
        background-color: #f0f0f2;
        margin: 0;
        padding: 0;
        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;
        
    }
    div {
        width: 600px;
        margin: 5em auto;
        padding: 2em;
        background-color: #fdfdff;
        border-radius: 0.5em;
        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);
    }
    a:link, a:visited {
        color: #38488f;
        text-decoration: none;
    }
    @media (max-width: 700px) {
        div {
            margin: 0 auto;
            width: auto;
        }
    }
    </style>    
</head>

<body>
<div>
    <h1>Example Domain</h1>
    <p>This domai

На всякий случай сохраним этот html, пригодится:

In [17]:
with open('example.com.txt', 'w', encoding='utf-8') as f:
    f.write(html)

In [19]:
print(dir(response))

['__abstractmethods__', '__class__', '__del__', '__delattr__', '__dict__', '__dir__', '__doc__', '__enter__', '__eq__', '__exit__', '__format__', '__ge__', '__getattribute__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__iter__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__next__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '_abc_impl', '_checkClosed', '_checkReadable', '_checkSeekable', '_checkWritable', '_check_close', '_close_conn', '_get_chunk_left', '_method', '_peek_chunked', '_read1_chunked', '_read_and_discard_trailer', '_read_chunked', '_read_next_chunk_size', '_read_status', '_readinto_chunked', '_safe_read', '_safe_readinto', 'begin', 'chunk_left', 'chunked', 'close', 'closed', 'code', 'debuglevel', 'detach', 'fileno', 'flush', 'fp', 'getcode', 'getheader', 'getheaders', 'geturl', 'headers', 'info', 'isatty', 'isclosed', 'length', 'msg', 'peek', 'read', 'read1', 'readable',

In [21]:
response.url

'http://example.com/'

In [23]:
response.msg

'OK'

In [25]:
response.code

200

In [27]:
response.headers

In [29]:
dict(response.headers)

{'Accept-Ranges': 'bytes',
 'Age': '167161',
 'Cache-Control': 'max-age=604800',
 'Content-Type': 'text/html; charset=UTF-8',
 'Date': 'Wed, 13 Nov 2024 10:00:43 GMT',
 'Etag': '"3147526947"',
 'Expires': 'Wed, 20 Nov 2024 10:00:43 GMT',
 'Last-Modified': 'Thu, 17 Oct 2019 07:18:26 GMT',
 'Server': 'ECAcc (nyd/D183)',
 'Vary': 'Accept-Encoding',
 'X-Cache': 'HIT',
 'Content-Length': '1256',
 'Connection': 'close'}

### requests

>HTTP for humans

In [31]:
import requests

In [33]:
response = requests.get('http://example.com')
response

<Response [200]>

In [35]:
print(dir(response))

['__attrs__', '__bool__', '__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__enter__', '__eq__', '__exit__', '__format__', '__ge__', '__getattribute__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__iter__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__nonzero__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__setstate__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', '_content', '_content_consumed', '_next', 'apparent_encoding', 'close', 'connection', 'content', 'cookies', 'elapsed', 'encoding', 'headers', 'history', 'is_permanent_redirect', 'is_redirect', 'iter_content', 'iter_lines', 'json', 'links', 'next', 'ok', 'raise_for_status', 'raw', 'reason', 'request', 'status_code', 'text', 'url']


In [37]:
response.url

'http://example.com/'

In [39]:
response.connection

In [41]:
response.headers

{'Content-Encoding': 'gzip', 'Age': '562422', 'Cache-Control': 'max-age=604800', 'Content-Type': 'text/html; charset=UTF-8', 'Date': 'Wed, 13 Nov 2024 10:01:54 GMT', 'Etag': '"3147526947+gzip"', 'Expires': 'Wed, 20 Nov 2024 10:01:54 GMT', 'Last-Modified': 'Thu, 17 Oct 2019 07:18:26 GMT', 'Server': 'ECAcc (nyd/D14F)', 'Vary': 'Accept-Encoding', 'X-Cache': 'HIT', 'Content-Length': '648'}

In [43]:
response.ok

True

In [45]:
response.status_code

200

In [47]:
response.encoding

'UTF-8'

In [49]:
response.links

{}

In [51]:
type(response.links)

dict

In [53]:
print(response.text)

<!doctype html>
<html>
<head>
    <title>Example Domain</title>

    <meta charset="utf-8" />
    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />
    <meta name="viewport" content="width=device-width, initial-scale=1" />
    <style type="text/css">
    body {
        background-color: #f0f0f2;
        margin: 0;
        padding: 0;
        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;
        
    }
    div {
        width: 600px;
        margin: 5em auto;
        padding: 2em;
        background-color: #fdfdff;
        border-radius: 0.5em;
        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);
    }
    a:link, a:visited {
        color: #38488f;
        text-decoration: none;
    }
    @media (max-width: 700px) {
        div {
            margin: 0 auto;
            width: auto;
        }
    }
    </style>    
</head>

<body>
<div>
    <h1>Example Domain</h1>
    <p>This domai

## Парсинг html

**Парсинг** - процесс разбора и систематизации информации и выделения полезных сущностей.

Популярные инструменты:
* re
* lxml
* BeautifulSoup

In [57]:
with open('example.com.txt', 'r', encoding='utf-8') as f:
    html = f.read()
print(html)

<!doctype html>
<html>
<head>
    <title>Example Domain</title>

    <meta charset="utf-8" />
    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />
    <meta name="viewport" content="width=device-width, initial-scale=1" />
    <style type="text/css">
    body {
        background-color: #f0f0f2;
        margin: 0;
        padding: 0;
        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;
        
    }
    div {
        width: 600px;
        margin: 5em auto;
        padding: 2em;
        background-color: #fdfdff;
        border-radius: 0.5em;
        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);
    }
    a:link, a:visited {
        color: #38488f;
        text-decoration: none;
    }
    @media (max-width: 700px) {
        div {
            margin: 0 auto;
            width: auto;
        }
    }
    </style>    
</head>

<body>
<div>
    <h1>Example Domain</h1>
    <p>This domai

### re

**Регулярные выражения (Regex)** – это строки, задающие шаблон для поиска определенных фрагментов в тексте. Помимо поиска, с помощью специальных Regex-шаблонов можно манипулировать текстовыми фрагментами – удалять и изменять подстроки частично или полностью.

Регулярные выражения состоят из набора литералов (букв и цифр) и метасимволов и выглядят примерно так:

```
r'(https?://)?(www\.)?youtube\.(com|nl)/watch\?v=([\w-]+)(&.*?)?(?=[^-\w&=%])'
```

Используя метасимволы, можно создавать сложные шаблоны, содержащие специальные конструкции для работы с определенными последовательностями и группами символов.

Regex-выражения применяют для обработки текстовых данных, в том числе в скриптах для веб-скрапинга. Кроме того, Regex используют в составе OCR-приложений для очистки отсканированного текста.



#### Регулярные выражения в Python

Для работы с регулярными выражениями в Python имеется модуль `re`.

Для экранирования служебных символов в шаблонах поиска и замены используют два способа – обратный слэш \ и «сырые» строки r''. Второй метод предпочтительнее – он позволяет избежать нагромождения слэшей в шаблонах.

In [1]:
import re

**Основные функции `re`**

`re.match()` – находит вхождение фрагмента в начале строки. Обычный формат использования – `re.match(r'шаблон', строка)`:

In [3]:
s = "кутка крякает, кукушка кукует, петух кукарекает"
match = re.match(r'ку', s)
print(match)

<re.Match object; span=(0, 2), match='ку'>


Этот код вернет `None`, несмотря на то, что в строке есть 5 фрагментов «ку». Это происходит потому, что оба фрагмента расположены не в начале строки.

`re.search()` – находит первое вхождение фрагмента в любом месте и возвращает объект `match`. Если в строке есть другие фрагменты, соответствующие запросу, `re.search` их проигнорирует. У `re.search` есть дополнительные методы:
- `.span()` – возвращает кортеж, содержащий начальную и конечную позиции искомого фрагмента
- `.string` – вернет строку, переданную в функцию `re.search`
- `.group()` – возвращает фрагмент строки, в котором было обнаружено совпадение

In [65]:
s = "oт топота копыт пыль по полю летит"
match = re.search(r'по', s)
print(match, match.span(), match.string, match.group(), sep='\n')

<re.Match object; span=(5, 7), match='по'>
(5, 7)
oт топота копыт пыль по полю летит
по


`re.findall()` – находит все вхождения фрагмента, в любом месте. Функция `re.findall()` учитывает регистр символов. Чтобы в результат вошли фрагменты с символами в другом регистре, применяют флаг `re.IGNORECASE`:

In [67]:
s = "Не видно, ликвидны акции или неликвидны."
match = re.findall(r'не', s, re.I)
print(match)

['Не', 'не']


`re.split()` – расщепляет строку по заданному шаблону. Количество расщеплений задается флагом – в этом примере от строки отделяется только первое слово:

In [69]:
s = "Обладаешь ли ты налогооблагаемой благодатью?"
res = re.split(r' ', s, 1)
res

['Обладаешь', 'ли ты налогооблагаемой благодатью?']

`re.sub()` – заменяет фрагмент в соответствии с шаблоном:

In [77]:
s = "Коала какао лениво лакала"
res = re.sub(r'Коала', 'Макака', s)
print(res)

Макака какао лениво лакала


`re.compile()` – создает объект из регулярного выражения. Применяется, если один и тот же поисковый шаблон используется в коде несколько раз:      


In [79]:
st = re.compile('угнал')
res1 = st.findall("Карл у Клары угнал Maclaren, а Клара у Карла угнала Corvette.")
res2 = st.findall("Карл у Клары угнал кораллы, а Клара у Карла угнала кларнет.")
print(res1, res2, sep='\n')

['угнал', 'угнал']
['угнал', 'угнал']


#### Основные метасимволы в Regex

- `[]`– используется для указания набора или диапазона символов

In [ ]:
re.findall(r'[с-я]', "Камер-юнкер юркнул в бункер", re.I)

['ю', 'ю', 'у', 'у']

In [ ]:
re.findall(r'[аж]', "ажиотаж, мандраж, багаж")

['а', 'ж', 'а', 'ж', 'а', 'а', 'ж', 'а', 'а', 'ж']

- `\` – указывает на начало последовательности (мы рассмотрим их ниже) или экранирует служебные символы
- `.` – выбирает любой символ, кроме новой строки `\n`
- `w` - any word character (буква, цифра или нижнее подчеркивание)
- `^` – проверяет, начинается ли строка с определенного символа / слова / набора символов.

    Например, `r'^Привет'` проверит, начинается ли строка с «Привет».
    
    Метасимвол `^` в наборе `[]` имеет другое значение – проверяет, отсутствуют ли в строке определенные символы (подробнее об этом ниже)
- `$` – проверяет, заканчивается ли строка в соответствии с шаблоном `r'До свиданья.$'`
- `*` – ноль или больше совпадений с шаблоном `r'ко.*аборация'`.
- `+` – одно и более совпадений `r'к.+ператив'`.
- `?` – ноль или одно совпадение `r'ф.?нтастика'`. Кроме того, нейтрализует «жадность» выражений, которые используют `.`, `*`, `+` для выбора любых символов.
- `{}` – точное число совпадений `r'Интерсте.{2}ар'`.
- `|`– любой из двух вариантов `r'уйду|останусь'`.
- `()` – захватывает группу для дальнейших манипуляций – `re.sub(r'(www)', r'\1.', "wwwwear-gear.com")`.
- `<>` – создает именованную группу – `re.search('(?P<группа1>\w+),(?P<группа2>\w+),(?P<группа3>\w+)', 'дом,улица,фонарь')`

#### Визуализация регулярных выражений

Чем сложнее регулярное выражение, тем труднее его правильно составить и протестировать. В интернете есть немало визуализаторов Regex, которые значительно упрощают эту задачу. Самый удобный ресурс – [regex101](https://regex101.com/) . Сайт предоставляет справочную и отладочную информацию, позволяет визуально тестировать шаблоны для поиска и замены. Помимо Python, поддерживает PHP, Java, Golang и JavaScript.

![regex](https://habrastorage.org/r/w1560/webt/l1/z1/9s/l1z19s49sk5bpc8vkmcbho7zgro.jpeg)

#### Регулярки для парсинга

Давайте забудем, что HTML -- дерево, и попробуем попарсить его, как строчку.

In [81]:
import re

In [83]:
h1 = re.findall(r'<h1>[\w ]+</h1>', html)
print(h1)

['<h1>Example Domain</h1>']


In [85]:
h1 = re.findall(r'<h1>([\w ]+)</h1>', html)
print(h1)

['Example Domain']


In [87]:
paragraphs = re.findall(r'<p>(.*)</p>', html)
paragraphs

['<a href="https://www.iana.org/domains/example">More information...</a>']

In [89]:
print(html)

<!doctype html>
<html>
<head>
    <title>Example Domain</title>

    <meta charset="utf-8" />
    <meta http-equiv="Content-type" content="text/html; charset=utf-8" />
    <meta name="viewport" content="width=device-width, initial-scale=1" />
    <style type="text/css">
    body {
        background-color: #f0f0f2;
        margin: 0;
        padding: 0;
        font-family: -apple-system, system-ui, BlinkMacSystemFont, "Segoe UI", "Open Sans", "Helvetica Neue", Helvetica, Arial, sans-serif;
        
    }
    div {
        width: 600px;
        margin: 5em auto;
        padding: 2em;
        background-color: #fdfdff;
        border-radius: 0.5em;
        box-shadow: 2px 3px 7px 2px rgba(0,0,0,0.02);
    }
    a:link, a:visited {
        color: #38488f;
        text-decoration: none;
    }
    @media (max-width: 700px) {
        div {
            margin: 0 auto;
            width: auto;
        }
    }
    </style>    
</head>

<body>
<div>
    <h1>Example Domain</h1>
    <p>This domai

Там же 2 параграфа, почему не нашёлся второй?

In [91]:
paragraphs = re.findall(r'<p>([\w\W]*)</p>', html)
paragraphs

['This domain is for use in illustrative examples in documents. You may use this\n    domain in literature without prior coordination or asking for permission.</p>\n    <p><a href="https://www.iana.org/domains/example">More information...</a>']

Опять плохо..

In [94]:
paragraphs = re.findall(r'<p>([\w\W]*?)</p>', html) # * - greedy; *? - lazy (non-greedy)
paragraphs

['This domain is for use in illustrative examples in documents. You may use this\n    domain in literature without prior coordination or asking for permission.',
 '<a href="https://www.iana.org/domains/example">More information...</a>']

Жесть, да?

### BeautifulSoup

Ещё одна библиотека, которая хорошо подходит для парсинга HTML.

In [96]:
from bs4 import BeautifulSoup

In [98]:
soup = BeautifulSoup(html, 'lxml')

In [100]:
paragraphs = soup.find_all('p')
paragraphs

[<p>This domain is for use in illustrative examples in documents. You may use this
     domain in literature without prior coordination or asking for permission.</p>,
 <p><a href="https://www.iana.org/domains/example">More information...</a></p>]

In [102]:
hrefs = soup.find_all('a')
hrefs

[<a href="https://www.iana.org/domains/example">More information...</a>]

In [104]:
hrefs = soup.find_all('a', href='https://www.iana.org/domains/example')
hrefs

[<a href="https://www.iana.org/domains/example">More information...</a>]

In [106]:
hrefs = soup.find_all('a', href='https://www.other-website.org/domains/example')
hrefs

[]

### Пример: парсинг списка страниц при помощи BS4

Цель тестового задания - получить часовые пояса всех городов России из википедии. Давайте попробуем найти страничку, где есть ссылки на все странички городов.

In [108]:
from requests.compat import urljoin, quote_plus, urlparse, unquote

In [110]:
# список городов России
url = "https://ru.wikipedia.org/wiki/%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D0%B3%D0%BE%D1%80%D0%BE%D0%B4%D0%BE%D0%B2_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8"

In [112]:
html = requests.get(url).content.decode('utf-8')
html

'<!DOCTYPE html>\n<html class="client-nojs" lang="ru" dir="ltr">\n<head>\n<meta charset="UTF-8">\n<title>Список городов России — Википедия</title>\n<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split(\'%2C\').forEach(function(pref){className=className.replace(new RegExp(\'(^| )\'+pref.replace(/-clientpref-\\w+$|[^\\w-]+/g,\'\')+\'-clientpref-\\\\w+( |$)\'),\'$1\'+pref+\'$2\');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\\t.","\xa0\\t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"6f6c55a5-fb78-48cb-888e-bb6979029d4e","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Список_городов_России","wgTitle":"Список городов России

In [114]:
soup = BeautifulSoup(html, features="html.parser")
soup

<!DOCTYPE html>

<html class="client-nojs" dir="ltr" lang="ru">
<head>
<meta charset="utf-8"/>
<title>Список городов России — Википедия</title>
<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\w+$|[^\w-]+/g,'')+'-clientpref-\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"6f6c55a5-fb78-48cb-888e-bb6979029d4e","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Список_городов_России","wgTitle":"Список городов России","wgCurRevisionId":14080

In [116]:
hrefs = soup.findAll('a')
hrefs

[<a id="top"></a>,
 <a href="/wiki/%D0%9A%D0%B0%D1%82%D0%B5%D0%B3%D0%BE%D1%80%D0%B8%D1%8F:%D0%98%D0%BD%D1%84%D0%BE%D1%80%D0%BC%D0%B0%D1%86%D0%B8%D0%BE%D0%BD%D0%BD%D1%8B%D0%B5_%D1%81%D0%BF%D0%B8%D1%81%D0%BA%D0%B8_%D0%BF%D0%BE_%D0%B0%D0%BB%D1%84%D0%B0%D0%B2%D0%B8%D1%82%D1%83" title="Информационные списки"><img alt="Информационные списки" class="mw-file-element" data-file-height="24" data-file-width="24" decoding="async" height="14" src="//upload.wikimedia.org/wikipedia/commons/thumb/7/74/QSicon_Formatierung_Blue.svg/14px-QSicon_Formatierung_Blue.svg.png" srcset="//upload.wikimedia.org/wikipedia/commons/thumb/7/74/QSicon_Formatierung_Blue.svg/21px-QSicon_Formatierung_Blue.svg.png 1.5x, //upload.wikimedia.org/wikipedia/commons/thumb/7/74/QSicon_Formatierung_Blue.svg/28px-QSicon_Formatierung_Blue.svg.png 2x" width="14"/></a>,
 <a href="/wiki/%D0%92%D0%B8%D0%BA%D0%B8%D0%BF%D0%B5%D0%B4%D0%B8%D1%8F:%D0%9F%D1%80%D0%BE%D0%B2%D0%B5%D1%80%D0%BA%D0%B0_%D1%81%D1%82%D0%B0%D1%82%D0%B5%D0%B9/%D0%9F%D0%

In [118]:
links = [urljoin(url, link.get('href')) for link in hrefs]
links

['https://ru.wikipedia.org/wiki/%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D0%B3%D0%BE%D1%80%D0%BE%D0%B4%D0%BE%D0%B2_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8',
 'https://ru.wikipedia.org/wiki/%D0%9A%D0%B0%D1%82%D0%B5%D0%B3%D0%BE%D1%80%D0%B8%D1%8F:%D0%98%D0%BD%D1%84%D0%BE%D1%80%D0%BC%D0%B0%D1%86%D0%B8%D0%BE%D0%BD%D0%BD%D1%8B%D0%B5_%D1%81%D0%BF%D0%B8%D1%81%D0%BA%D0%B8_%D0%BF%D0%BE_%D0%B0%D0%BB%D1%84%D0%B0%D0%B2%D0%B8%D1%82%D1%83',
 'https://ru.wikipedia.org/wiki/%D0%92%D0%B8%D0%BA%D0%B8%D0%BF%D0%B5%D0%B4%D0%B8%D1%8F:%D0%9F%D1%80%D0%BE%D0%B2%D0%B5%D1%80%D0%BA%D0%B0_%D1%81%D1%82%D0%B0%D1%82%D0%B5%D0%B9/%D0%9F%D0%BE%D1%8F%D1%81%D0%BD%D0%B5%D0%BD%D0%B8%D0%B5_%D0%B4%D0%BB%D1%8F_%D1%87%D0%B8%D1%82%D0%B0%D1%82%D0%B5%D0%BB%D0%B5%D0%B9',
 'https://ru.wikipedia.org/w/index.php?title=%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D0%B3%D0%BE%D1%80%D0%BE%D0%B4%D0%BE%D0%B2_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8&stable=1',
 'https://ru.wikipedia.org/w/index.php?title=%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D0%B3%D0%BE%D1%8

Ура, получили список ссылок на этой страничке! Но не все они - ссылки на города. Часто в таких случаях есть большое количество ненужных ссылок, например, на изображения или ещё куда-то.

[Тут про магию, как мы получаем нормальный текст ссылки](https://stackoverflow.com/questions/16566069/url-decode-utf-8-in-python)


In [120]:
for i in range(6):
    print(unquote(links[i*5]))

https://ru.wikipedia.org/wiki/Список_городов_России
https://ru.wikipedia.org/wiki/Список_городов_России#mw-head
https://ru.wikipedia.org/wiki/Список_городов_России#Города_в_составе_городов_федерального_значения
https://ru.wikipedia.org/wiki/Файл:Coat_of_Arms_of_Abaza_(Khakassia).png
https://ru.wikipedia.org/wiki/Хакасия
https://ru.wikipedia.org/wiki/Абинск


In [128]:
len(links)

4043

In [130]:
def filter(links, keyword='ru.wikipedia.org/wiki/', stopwords=['Список', 'Файл', 'списки', '2020', '1380', 'Проверка_статей']):
    filtered_links = []
    new_links = []
    for link in links:
        new_link = unquote(link)
        if keyword in new_link:
            flag_check = True
            for word in stopwords:
                if word in new_link:
                    flag_check = False
            if flag_check:
                filtered_links.append(link)
                new_links.append(new_link)
    return filtered_links, new_links

In [132]:
filtered_links, new_filtered_links = filter(links)
new_filtered_links

['https://ru.wikipedia.org/wiki/Абаза_(город)',
 'https://ru.wikipedia.org/wiki/Хакасия',
 'https://ru.wikipedia.org/wiki/Абакан',
 'https://ru.wikipedia.org/wiki/Хакасия',
 'https://ru.wikipedia.org/wiki/Абдулино',
 'https://ru.wikipedia.org/wiki/Оренбургская_область',
 'https://ru.wikipedia.org/wiki/Абинск',
 'https://ru.wikipedia.org/wiki/Краснодарский_край',
 'https://ru.wikipedia.org/wiki/Агидель_(город)',
 'https://ru.wikipedia.org/wiki/Башкортостан',
 'https://ru.wikipedia.org/wiki/Агрыз',
 'https://ru.wikipedia.org/wiki/Татарстан',
 'https://ru.wikipedia.org/wiki/Адыгейск',
 'https://ru.wikipedia.org/wiki/Адыгея',
 'https://ru.wikipedia.org/wiki/Азнакаево',
 'https://ru.wikipedia.org/wiki/Татарстан',
 'https://ru.wikipedia.org/wiki/Азов',
 'https://ru.wikipedia.org/wiki/Ростовская_область',
 'https://ru.wikipedia.org/wiki/Ак-Довурак',
 'https://ru.wikipedia.org/wiki/Тыва',
 'https://ru.wikipedia.org/wiki/Аксай_(Ростовская_область)',
 'https://ru.wikipedia.org/wiki/Ростовская_об

In [134]:
len(new_filtered_links)

2719

In [136]:
len(set(new_filtered_links))

1622

Получается, можем удалить дубликаты и получить уже почти что список городов России

На самом деле, городов России порядка 1150, значит, надо ещё аккуратно посидеть над ссылками, чтобы убрать лишние

In [138]:
new_filtered_links[0]

'https://ru.wikipedia.org/wiki/Абаза_(город)'

Теперь надо разобраться, как получить из [этой ссылки](https://ru.wikipedia.org/wiki/%D0%90%D0%B1%D0%B0%D0%B7%D0%B0_(%D0%B3%D0%BE%D1%80%D0%BE%D0%B4)) название города и часовой пояс

In [140]:
html = requests.get(new_filtered_links[0]).content.decode('utf-8')
html

'<!DOCTYPE html>\n<html class="client-nojs" lang="ru" dir="ltr">\n<head>\n<meta charset="UTF-8">\n<title>Абаза (город) — Википедия</title>\n<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split(\'%2C\').forEach(function(pref){className=className.replace(new RegExp(\'(^| )\'+pref.replace(/-clientpref-\\w+$|[^\\w-]+/g,\'\')+\'-clientpref-\\\\w+( |$)\'),\'$1\'+pref+\'$2\');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\\t.","\xa0\\t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"eaa676ca-611d-4e5e-a9d8-4155c1956339","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Абаза_(город)","wgTitle":"Абаза (город)","wgCurRevisionId":1406

Давайте изучим ссылку и найдем, где хранится Часовой Пояс

In [142]:
soup = BeautifulSoup(html, features="html.parser")
soup

<!DOCTYPE html>

<html class="client-nojs" dir="ltr" lang="ru">
<head>
<meta charset="utf-8"/>
<title>Абаза (город) — Википедия</title>
<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\w+$|[^\w-]+/g,'')+'-clientpref-\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"eaa676ca-611d-4e5e-a9d8-4155c1956339","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Абаза_(город)","wgTitle":"Абаза (город)","wgCurRevisionId":140697576,"wgRevisionId":1406

In [144]:
match = re.search(r'<a href="/wiki/UTC%', html)

st, en = match.span()

In [146]:
html[en:(en+50)]

'2B7:00" title="UTC+7:00">UTC+7:00</a></span></td>\n'

In [148]:
utc = re.findall(r'UTC\+.{1}:00', html)
print(utc[0])

UTC+7:00


Дальше нам останется только запустить цикл и закончить задание :)

## Extra

Помимо рассмотренных библиотек есть удобный инструмент для тестирования веб-приложений [Selenium WebDriver](https://www.selenium.dev/documentation/webdriver/) и его питоновская обертка [selenium-python](https://selenium-python.readthedocs.io/).

Классная вещь, для простого скрапинга и парсинга - перебор (создана не для этого по сути), но в некоторых случаях спасает - например, если на сайте динамическая генерация контента.

## Производительность

In [169]:
%timeit re.findall(r'<p>([\w\W]*?)</p>', html)
%timeit tree.xpath('//p')
%timeit soup.find_all('p')

1.13 ms ± 93.3 μs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)
161 μs ± 10.3 μs per loop (mean ± std. dev. of 7 runs, 10,000 loops each)
2.28 ms ± 541 μs per loop (mean ± std. dev. of 7 runs, 100 loops each)


**Мораль:** `regex` -- это быстро.

`BeautifulSoup` чуть дольше `lxml`, т.к. он для удобства работы преобразует документ в свой внутренний формат -- собственно, суп.

# Extra: `lxml`

Воспользуемся библиотекой, которая знает про структуру XML (и HTML).

In [151]:
from lxml import etree
from io import StringIO, BytesIO

In [153]:
parser = etree.HTMLParser()
tree = etree.parse(StringIO(html), parser)
tree

In [155]:
print(dir(tree))

['__class__', '__copy__', '__deepcopy__', '__delattr__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__ne__', '__new__', '__pyx_vtable__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '_setroot', 'docinfo', 'find', 'findall', 'findtext', 'getelementpath', 'getiterator', 'getpath', 'getroot', 'iter', 'iterfind', 'parse', 'parser', 'relaxng', 'write', 'write_c14n', 'xinclude', 'xmlschema', 'xpath', 'xslt']


In [157]:
print(tree.getroot())

<Element html at 0x20ae27c2e40>


In [159]:
print(etree.tostring(tree.getroot(), pretty_print=True, method='html'))

b'<html class="client-nojs" lang="ru" dir="ltr">\n<head>\n<meta charset="UTF-8">\n<title>&#1040;&#1073;&#1072;&#1079;&#1072; (&#1075;&#1086;&#1088;&#1086;&#1076;) &#8212; &#1042;&#1080;&#1082;&#1080;&#1087;&#1077;&#1076;&#1080;&#1103;</title>\n<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split(\'%2C\').forEach(function(pref){className=className.replace(new RegExp(\'(^| )\'+pref.replace(/-clientpref-\\w+$|[^\\w-]+/g,\'\')+\'-clientpref-\\\\w+( |$)\'),\'$1\'+pref+\'$2\');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\\t.","&#160;\\t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","&#1103;&#1085;&#1074;&#1072;&#1088;&#1100;","&#1092;&#1077;&#1074;&#1088;&#1072;&#1083;&#1100;","&#1084;&#1072;&#1088;&#1090;","&#1072;&#1087;&#1088;&#1077;&#1083;&#1100;","&#1084;&#1072;&#1081;","&#1080;&#1102;

In [161]:
paragraphs = tree.xpath('//p')
for p in paragraphs:
    print(p.text)

None
Составляет 
Название города происходит от сокращения в виде 
Город расположен в межгорной котловине, в верхнем течении реки 
Железнодорожной веткой через станцию 
Город Абаза возник в 1856 году  в связи с разработкой 
В начале 1920 года была создана Абакано-Заводская волость. В 1921 году волостной съезд народных депутатов принял решение о переименовании деревни Абакано-Заводская в село Абаза. С 1926 по 1957 годы месторождение не эксплуатировалось. В 1956 году Абазе был присвоен статус рабочего посёлка. В 1957 году добыча руды была возобновлена. В 1966 году посёлок был преобразован в город районного значения, а в 2003 году стал городом республиканского подчинения.

В 1981 году в  Абазе происходили съёмки фильма «
Численность населения на 1 января 2021 год: 14 816 человек.

По оценке Росстата на 1 января 2024 года по численности населения город находился на 858-м месте из 1119
Структуру органов местного самоуправления города Абазы составляют
None
None
Добыча железной руды осуществля

In [163]:
for p in paragraphs:
    print(etree.tostring(p, pretty_print=True, method='html'))

b'<p><b>&#1040;&#1073;&#1072;&#1079;&#1072;&#769;</b><sup id="cite_ref-3" class="reference"><a href="#cite_note-3"><span class="cite-bracket">[</span>3<span class="cite-bracket">]</span></a></sup>&#160;&#8212; &#1075;&#1086;&#1088;&#1086;&#1076; &#1074; <a href="/wiki/%D0%A5%D0%B0%D0%BA%D0%B0%D1%81%D0%B8%D1%8F" title="&#1061;&#1072;&#1082;&#1072;&#1089;&#1080;&#1103;">&#1056;&#1077;&#1089;&#1087;&#1091;&#1073;&#1083;&#1080;&#1082;&#1077; &#1061;&#1072;&#1082;&#1072;&#1089;&#1080;&#1103;</a> <a href="/wiki/%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D1%8F" title="&#1056;&#1086;&#1089;&#1089;&#1080;&#1103;">&#1056;&#1086;&#1089;&#1089;&#1080;&#1080;</a>.\n</p>\n'
b'<p>&#1057;&#1086;&#1089;&#1090;&#1072;&#1074;&#1083;&#1103;&#1077;&#1090; <a href="/wiki/%D0%90%D0%B4%D0%BC%D0%B8%D0%BD%D0%B8%D1%81%D1%82%D1%80%D0%B0%D1%82%D0%B8%D0%B2%D0%BD%D0%BE-%D1%82%D0%B5%D1%80%D1%80%D0%B8%D1%82%D0%BE%D1%80%D0%B8%D0%B0%D0%BB%D1%8C%D0%BD%D0%BE%D0%B5_%D0%B4%D0%B5%D0%BB%D0%B5%D0%BD%D0%B8%D0%B5_%D0%A5%D0%B0%D0%BA%D0%B0%D1

In [165]:
hrefs = tree.xpath('//a')
for href in hrefs:
    print(href.text, href.attrib)

None {'id': 'top'}
52°39′00″ с. ш. 90°05′00″ в. д. {'class': 'mw-kartographer-maplink', 'data-mw-kartographer': 'maplink', 'data-style': 'osm-intl', 'href': '/wiki/%D0%A1%D0%BB%D1%83%D0%B6%D0%B5%D0%B1%D0%BD%D0%B0%D1%8F:Map/12/52.65/90.083333333333/ru', 'data-zoom': '12', 'data-lat': '52.65', 'data-lon': '90.083333333333', 'data-lang': 'ru', 'data-overlays': '["_1a080d243b9b706712d57151d853e23e40637b45"]'}
None {'class': 'external text', 'href': 'https://geohack.toolforge.org/geohack.php?language=ru&pagename=%D0%90%D0%B1%D0%B0%D0%B7%D0%B0_(%D0%B3%D0%BE%D1%80%D0%BE%D0%B4)&params=52.65_0_0_N_90.083333333333_0_0_E_scale:100000_region:RU_type:city'}
None {'rel': 'nofollow', 'class': 'external text', 'href': 'https://maps.google.com/maps?ll=52.65,90.083333333333&q=52.65,90.083333333333&spn=0.1,0.1&t=h&hl=ru'}
None {'rel': 'nofollow', 'class': 'external text', 'href': 'https://yandex.ru/maps/?ll=90.083333333333,52.65&pt=90.083333333333,52.65&spn=0.1,0.1&l=sat,skl'}
None {'rel': 'nofollow', 'c

In [167]:
specific_hrefs = tree.xpath('//a[@href="https://www.iana.org/domains/example"]')
specific_hrefs

[]

# Extra: `scrapy`

Будем парсить сайт с архивом курсов криптовалют: https://coinmarketcap.com/.

Хочется открыть [historical snapshots](https://coinmarketcap.com/historical/) и для каждой недели выгрузить полную табличку.

>**Важно!**
>
>Совершенно не обязательно понимать, что будет происходить дальше.
>
>**Мораль** - есть фреймворки, которые полностью берут на себя получение и парсинг HTML.
>
>А ещё они умеют распараллеливать процесс, вставлять случайные задержки (чтобы серверы не подумали, что вы робот и не заблокировали ваши запросы) и удобно экспортировать полученные данные (например, в базу данных). И многое другое. <br>И всё это контролируется `scrapy.cfg` -- одним конфигурационным файлом.
>
>Вам остаётся только указать, какие куски текста надо выцеплять. И в какую базу класть. Ну, почти. :)



In [ ]:
%%bash
pip install scrapy

In [171]:
import scrapy

In [ ]:
%%bash
rm -rf coinmarketcap

In [ ]:
%%bash
scrapy startproject coinmarketcap

New Scrapy project 'coinmarketcap', using template directory '/usr/local/lib/python3.9/dist-packages/scrapy/templates/project', created in:
    /content/coinmarketcap

You can start your first spider with:
    cd coinmarketcap
    scrapy genspider example example.com


Что там внутри?

In [ ]:
%%bash
cd coinmarketcap
ls -R

.:
coinmarketcap
scrapy.cfg

./coinmarketcap:
__init__.py
items.py
middlewares.py
pipelines.py
settings.py
spiders

./coinmarketcap/spiders:
__init__.py


Специальная функция, чтобы из ноутбука формировать код в проекте scrapy:

In [173]:
def dump_to(path):
    with open(path, 'w') as f:
        f.write(_i)  # _i это "последний выполненный Input" в iPython

>**Внимание!**
>
>Следующие ячейки при выполнении не будут делать ничего полезного.
>Мы просто помещаем код в *Input*, а потом перекладываем его в нужный файл.

### Item

Cперва определим, что хотим собирать

In [ ]:
# -*- coding:utf8 -*-

import scrapy


class CurrencyItem(scrapy.Item):
    date = scrapy.Field()
    name = scrapy.Field()
    symbol = scrapy.Field()
    market_cap = scrapy.Field()
    price = scrapy.Field()

In [ ]:
dump_to('./coinmarketcap/coinmarketcap/items.py')

### Spider

Определим **спайдеры** - процессы, которые собирают Item'ы.

In [ ]:
# -*- coding:utf8 -*-

from scrapy import Request
from scrapy.spiders import CrawlSpider, Rule
from scrapy.linkextractors import LinkExtractor
from scrapy.loader.processors import Join
from scrapy.loader import ItemLoader
from scrapy.selector import Selector
from coinmarketcap.items import CurrencyItem


class CurrencyLoader(ItemLoader):
    pass


class WeeklySpider(CrawlSpider):
    name = 'weekly'
    allowed_domains = ['coinmarketcap.com']
    start_urls = ['https://coinmarketcap.com/historical/']
    only_2018_april_regex = '/201904[0-9]{2}' # full history parsing takes ~4 hrs

    rules = (
        Rule(LinkExtractor(allow=(only_2018_april_regex, )), callback='parse_weekly_report', follow=False),
    )

    def parse_weekly_report(self, response):

        hxs = Selector(response)
        items_html = hxs.xpath('//table//tr')
        #print(len(items_html),type(items_html),dir(items_html))
        #print(items_html)
        items = []
        item_names = items_html.xpath('//td[@class="cmc-table__cell cmc-table__cell--sticky cmc-table__cell--sortable cmc-table__cell--left cmc-table__cell--sort-by__name"]//div//a/text()').extract()
        item_symbols = items_html.xpath('//td[@class="cmc-table__cell cmc-table__cell--sortable cmc-table__cell--left cmc-table__cell--sort-by__symbol"]//div/text()').extract()
        item_caps = items_html.xpath('//td[@class="cmc-table__cell cmc-table__cell--sortable cmc-table__cell--right cmc-table__cell--sort-by__market-cap"]//div/text()').extract()
        item_prices = items_html.xpath('//td[@class="cmc-table__cell cmc-table__cell--sortable cmc-table__cell--right cmc-table__cell--sort-by__price"]//div/text()').extract()
        #print(response.request.url)
        #print(len(item_prices),item_prices)

        for i in range(200):

            item = CurrencyItem()
            item['date'] = response.request.url.split('/')[-2]
            item['name'] = item_names[i]
            item['symbol'] = item_symbols[i]
            item['market_cap'] = item_caps[i]
            item['price'] = item_prices[i]

            yield item


ModuleNotFoundError: ignored

In [ ]:
dump_to('./coinmarketcap/coinmarketcap/spiders/weekly.py')

### Pipeline

Определяем конвейер, в котором будем делать с данными что-то полезное, например, экспорт в БД.

In [ ]:
# -*- coding: utf-8 -*-

import os, logging
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import create_engine, Table, Column, Integer, String, Date, MetaData, ForeignKey
from sqlalchemy.engine.url import URL
from sqlalchemy.orm import sessionmaker
from sqlalchemy.pool import NullPool
from scrapy.exceptions import DropItem
from scrapy import signals
from coinmarketcap.items import CurrencyItem
import pandas as pd
from collections import Counter

logger = logging.getLogger(__name__)

DeclarativeBase = declarative_base()

class Currency(DeclarativeBase):
    __tablename__ = 'currency'
    __table_args__ = {'sqlite_autoincrement': True}

    id = Column('id', Integer, primary_key=True)
    date = Column('date', Date)
    name = Column('name', String)
    symbol = Column('symbol', String)
    market_cap = Column('market_cap', String)
    price = Column('price', String)

    def __init__(self, item):
        self.date = pd.to_datetime(item['date'], format='%Y%m%d')
        self.name = item['name']
        self.symbol = item['symbol']
        self.market_cap = item['market_cap']
        self.price = item['price']

    def __repr__(self):
        return "<Currency({0}, {1}, {2})>".format(self.id, self.symbol, self.market_cap)


class SqlitePipeline(object):
    def __init__(self, settings):
        self.database = settings.get('DATABASE')
        self.sessions = {}

    @classmethod
    def from_crawler(cls, crawler):
        pipeline = cls(crawler.settings)
        crawler.signals.connect(pipeline.spider_closed, signals.spider_closed)
        crawler.signals.connect(pipeline.spider_opened, signals.spider_opened)
        return pipeline

    def create_engine(self):
        engine = create_engine(URL(**self.database), poolclass=NullPool)
        return engine

    def create_tables(self, engine):
        DeclarativeBase.metadata.create_all(engine, checkfirst=True)

    def create_session(self, engine):
        session = sessionmaker(bind=engine)()
        return session

    def spider_opened(self, spider):
        engine = self.create_engine()
        self.create_tables(engine)
        session = self.create_session(engine)
        self.sessions[spider] = session

    def spider_closed(self, spider):
        session = self.sessions.pop(spider)
        session.close()

    def process_item(self, item, spider):
        session = self.sessions[spider]
        currency = Currency(item)
        link_exists = session.query(Currency).filter_by(symbol=item['symbol'], date=item['date']).first() is not None

        if link_exists:
            logger.info('Item {} is in db'.format(currency))
            return item

        try:
            session.add(currency)
            session.commit()
            logger.info('Item {} stored in db'.format(currency))
        except Exception as e:
            logger.info('Failed to add {} to db'.format(currency))
            session.rollback()
            raise e

        return item

ModuleNotFoundError: ignored

In [ ]:
dump_to('./coinmarketcap/coinmarketcap/pipelines.py')

### Settings

Указываем общие настройки `scrapy`.

In [ ]:
# -*- coding: utf-8 -*-

# Scrapy settings for coinmarketcap project
#
# For simplicity, this file contains only settings considered important or
# commonly used. You can find more settings consulting the documentation:
#
#     https://doc.scrapy.org/en/latest/topics/settings.html
#     https://doc.scrapy.org/en/latest/topics/downloader-middleware.html
#     https://doc.scrapy.org/en/latest/topics/spider-middleware.html

BOT_NAME = 'coinmarketcap'

SPIDER_MODULES = ['coinmarketcap.spiders']
NEWSPIDER_MODULE = 'coinmarketcap.spiders'

DATABASE = {
    'drivername': 'sqlite',
    # 'host': 'localhost',
    # 'port': '5432',
    # 'username': 'YOUR_USERNAME',
    # 'password': 'YOUR_PASSWORD',
    'database': 'weekly.sqlite'
}

# Crawl responsibly by identifying yourself (and your website) on the user-agent
USER_AGENT = '%s' % (BOT_NAME)

# Obey robots.txt rules
# ROBOTSTXT_OBEY = True

# Configure maximum concurrent requests performed by Scrapy (default: 16)
CONCURRENT_REQUESTS = 1

# Configure a delay for requests for the same website (default: 0)
# See https://doc.scrapy.org/en/latest/topics/settings.html#download-delay
# See also autothrottle settings and docs
#DOWNLOAD_DELAY = 3
# The download delay setting will honor only one of:
#CONCURRENT_REQUESTS_PER_DOMAIN = 16
#CONCURRENT_REQUESTS_PER_IP = 16

# Disable cookies (enabled by default)
#COOKIES_ENABLED = False

# Disable Telnet Console (enabled by default)
#TELNETCONSOLE_ENABLED = False

# Override the default request headers:
#DEFAULT_REQUEST_HEADERS = {
#   'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
#   'Accept-Language': 'en',
#}

# Enable or disable spider middlewares
# See https://doc.scrapy.org/en/latest/topics/spider-middleware.html
#SPIDER_MIDDLEWARES = {
#    'coinmarketcap.middlewares.CoinmarketcapSpiderMiddleware': 543,
#}

# Enable or disable downloader middlewares
# See https://doc.scrapy.org/en/latest/topics/downloader-middleware.html
#DOWNLOADER_MIDDLEWARES = {
#    'coinmarketcap.middlewares.CoinmarketcapDownloaderMiddleware': 543,
#}

# Enable or disable extensions
# See https://doc.scrapy.org/en/latest/topics/extensions.html
#EXTENSIONS = {
#    'scrapy.extensions.telnet.TelnetConsole': None,
#}

# Configure item pipelines
# See https://doc.scrapy.org/en/latest/topics/item-pipeline.html
ITEM_PIPELINES = {
   'coinmarketcap.pipelines.SqlitePipeline': 300,
}

# Enable and configure the AutoThrottle extension (disabled by default)
# See https://doc.scrapy.org/en/latest/topics/autothrottle.html
AUTOTHROTTLE_ENABLED = False
# The initial download delay
AUTOTHROTTLE_START_DELAY = 5
# The maximum download delay to be set in case of high latencies
AUTOTHROTTLE_MAX_DELAY = 60
# The average number of requests Scrapy should be sending in parallel to
# each remote server
#AUTOTHROTTLE_TARGET_CONCURRENCY = 1.0
# Enable showing throttling stats for every response received:
#AUTOTHROTTLE_DEBUG = False

# Enable and configure HTTP caching (disabled by default)
# See https://doc.scrapy.org/en/latest/topics/downloader-middleware.html#httpcache-middleware-settings
#HTTPCACHE_ENABLED = True
#HTTPCACHE_EXPIRATION_SECS = 0
#HTTPCACHE_DIR = 'httpcache'
#HTTPCACHE_IGNORE_HTTP_CODES = []
#HTTPCACHE_STORAGE = 'scrapy.extensions.httpcache.FilesystemCacheStorage'

LOG_FILE = 'crawling.log'

In [ ]:
dump_to('./coinmarketcap/coinmarketcap/settings.py')

Посмотрим на структуру scrapy проекта ещё раз

In [ ]:
%%bash
cd coinmarketcap
ls -R

.:
coinmarketcap
scrapy.cfg

./coinmarketcap:
__init__.py
items.py
middlewares.py
pipelines.py
settings.py
spiders

./coinmarketcap/spiders:
__init__.py
weekly.py


### Запуск

Все подготовили, теперь запустим паука!

In [ ]:
%%timeit -n 1 -r 1
%%bash
cd coinmarketcap;
scrapy crawl weekly

/usr/local/lib/python3.9/dist-packages/scrapy/utils/request.py:232: ScrapyDeprecationWarning: '2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a future version of Scrapy.

See the documentation of the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting for information on how to handle this deprecation.
  return cls(crawler)


15.8 s ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


Посмотрим, что получилось:

In [ ]:
import sqlite3
import pandas as pd

connection = sqlite3.connect('./coinmarketcap/weekly.sqlite')

df = pd.read_sql_query("SELECT * FROM currency", connection)
print(df.shape)
df.head()

(800, 6)


id        date      name symbol          market_cap      price
0   1  2019-04-07       BTC    BTC  $91,674,230,185.93  $5,198.90
1   2  2019-04-07   Bitcoin    ETH  $18,424,576,820.42    $174.53
2   3  2019-04-07       ETH    XRP  $15,021,731,304.72    $0.3599
3   4  2019-04-07  Ethereum    BCH   $5,662,007,844.39    $319.60
4   5  2019-04-07       XRP    LTC   $5,653,406,711.33     $92.31